# 2D OCC Geometries in Netgen

We have exported a wide varyity of toolsets from the open source geometry kernel [OpenCascade](https://opencascade.com). They are available via the Netgen Python interface in `netgen.occ`:

In [1]:
from netgen.occ import *
from ngsolve import *
from ngsolve.webgui import Draw

In 2D we work with the `WorkPlane` object, it lets us define geometries on a 2D Plane in 3D space.

In [2]:
wp = WorkPlane()
wp.Circle(0,0,1)
c = wp.Face()
wp.MoveTo(2,0).Rectangle(1,1)
r = wp.Face()
wp.MoveTo(0,2).LineTo(1,2).ArcTo(1,3,(1,1)).Close()
t = wp.Face()
c.name = "c"
r.name = "r"
t.name = "t"

shape = Compound([c,r,t])
Draw(shape)

WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'ngsolve_version': 'Netgen x.x', 'mesh_dim': …

BaseWebGuiScene

A range of predefined functions is available on the workplane:

In [3]:
help(wp)

Help on WorkPlane in module netgen.libngpy._NgOCC object:

class WorkPlane(pybind11_builtins.pybind11_object)
 |  Method resolution order:
 |      WorkPlane
 |      pybind11_builtins.pybind11_object
 |      builtins.object
 |  
 |  Methods defined here:
 |  
 |  Arc(...)
 |      Arc(self: netgen.libngpy._NgOCC.WorkPlane, r: float, ang: float) -> netgen.libngpy._NgOCC.WorkPlane
 |      
 |      draw arc tangential to current pos/dir, of radius 'r' and angle 'ang', draw to the left/right if ang is positive/negative
 |  
 |  ArcTo(...)
 |      ArcTo(self: netgen.libngpy._NgOCC.WorkPlane, arg0: float, arg1: float, arg2: netgen.libngpy._NgOCC.gp_Vec2d) -> netgen.libngpy._NgOCC.WorkPlane
 |  
 |  Circle(...)
 |      Circle(*args, **kwargs)
 |      Overloaded function.
 |      
 |      1. Circle(self: netgen.libngpy._NgOCC.WorkPlane, h: float, v: float, r: float) -> netgen.libngpy._NgOCC.WorkPlane
 |      
 |      draw circle with center (h,v) and radius 'r'
 |      
 |      2. Circle(self: n

We can also move objects around and apply boolean operations on them. Note that glue leaves the interface between two domains and keeps the two domains, whereas the `+` operator creates one domain

<div class="alert alert-block alert-warning"><b>Important:</b> Operations in the OCC wrapper always create copies of the object and do not modify the original.</div>

Here we see how to give names and meshsizes to shapes, when operations are done properties are prolonged (as good as possible)

In [4]:
d1 = c - r.Move((-2,0,0))
e1 = d1.edges.Nearest((0,0.5,0))
# restrict meshsize at edges
e1.maxh = 0.1
v = d1.vertices.Nearest((1,0,0))
# or at vertices
v.maxh = 0.02
d1.faces.name = "circle"
d2 = r + t.Move((2,-1,0))
d2.faces.name = "d2"
d2.edges.Min(Y).name = "bottom"
d3 = Glue([r, t.Move((2,-1,0))])
d4 = (c * r.Move((-2,0,0))).Move((-2,0,0))

d = Compound([d1, d2, d3.Move((-2,0,0)), d4], separate_layers=False)
Draw(d)

WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'ngsolve_version': 'Netgen x.x', 'mesh_dim': …

BaseWebGuiScene

These objects are still just thin wrapper around OpenCascade objects, to mesh it with Netgen we need to create a Netgen `OCCGeometry` from it. For a 2D geometry we additionally need to give the dimension.
We see that, because of the `separate_layers=True` setting in the compound the meshsize in `d2` is not influenced by the finer edge mesh in `d1`

In [9]:
geo = OCCGeometry(d, dim=2)
mesh = Mesh(geo.GenerateMesh(maxh=0.3))
mesh.Curve(3)
Draw(mesh)

WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.2…

BaseWebGuiScene

Splines are also possible, [Geom2dAPI_Interpolate](https://dev.opencascade.org/doc/refman/html/class_geom2d_a_p_i___interpolate.html) is used internally:

In [6]:
wp.MoveTo(0,0)
wp.Spline(points=[(1,-1), (2,0), (1,1)], periodic=False, tangents={1: (1,0)})
s = wp.Close().Face()
Draw(s)

WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'ngsolve_version': 'Netgen x.x', 'mesh_dim': …

BaseWebGuiScene

## Periodicity

We allow to identify periodic and anisotropic mesh regions by using the `TopoDS_Shape.Idenfity` method, if the transformation is only between two edges and only a translation we can skip the transformation argument, else we have to provide the transformation from shape1 to shape2


<div class="alert alert-block alert-warning"><b>Important:</b> If one point is identified by multiple identifications (for example xmin -> xmax and ymin -> ymax) the identifications must have different names! </div>

In [10]:
r = Rectangle(1,1).Face()
r.edges.Min(X).Identify(r.edges.Max(X),
                        "periodicx",
                        IdentificationType.PERIODIC)
r.edges.Min(Y).Identify(r.edges.Max(Y),
                        "periodicy",
                        IdentificationType.PERIODIC)
geo = OCCGeometry(r, dim=2)
mesh = Mesh(geo.GenerateMesh(maxh=0.2))

# Code to draw identifications
plist = []
for pair in mesh.ngmesh.GetIdentifications():
    plist += list(mesh.vertices[pair[0]-1].point)
    plist.append(0)
    plist += list(mesh.vertices[pair[1]-1].point)
    plist.append(0)
Draw(mesh, objects=[{"type" : "lines", "position" : plist, "name": "identification", "color": "purple"}])

WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.2…

BaseWebGuiScene

## Anisotropic mesh regions with Closesurfaces

The identification type CLOSESURFACES can be used to trigger anisotropic meshing for thin layers. `mesh.ZRefine` can then be called to refine the layers in identification direction by giving the slices as a list.

In [8]:
r = Rectangle(0.1,1).Face()
r.edges.Min(X).Identify(r.edges.Max(X),
                        "cs",
                        IdentificationType.CLOSESURFACES)
geo = OCCGeometry(r, dim=2)
mesh = geo.GenerateMesh(maxh=0.2)
mesh.ZRefine("cs", [0.01, 0.2, 0.5])
mesh = Mesh(mesh)
Draw(mesh)

WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.2…

BaseWebGuiScene